In [1]:
import pyvista as pv
import numpy as np

import pyvista as pv

pv.set_jupyter_backend("static")

In [2]:
def orthogonal_frame(vectors):
    """Compute tangent vectors to a normal vector field.

    This routine assumes that the 3D "normal" vectors are normalized.
    It is based on the 2017 paper from Pixar,
    "Building an orthonormal basis, revisited".

    Parameters
    ----------
    normals
        (N,3) or (N,3) normals `n_i`, i.e. unit-norm 3D vectors.
    """
    x, y, z = vectors[..., 0], vectors[..., 1], vectors[..., 2]
    s = (2 * (z >= 0)) - 1.0  # = z.sign(), but =1. if z=0.
    a = -1 / (s + z)
    b = x * y * a
    u = np.stack((1 + s * x * x * a, s * b, -s * x), dim=-1)
    v = np.stack((b, s + y * y * a, -y), dim=-1)
    return u, v

In [3]:
n_u, n_v = 16, 8
tube_radius = 0.8
closed_loop = True

u = np.linspace(0, 2 * np.pi, n_u, endpoint=not closed_loop)

x = np.sin(u) + 2 * np.sin(2 * u)
y = np.cos(u) - 2 * np.cos(2 * u)
z = -np.sin(3 * u)

curve_points = np.stack((x, y, z), axis=1)

In [ ]:
cloud = pv.PolyData(curve_points)
pl = pv.Plotter(window_size=[400, 400])
point_size = 30 * 10 / np.sqrt(len(curve_points))
pl.add_mesh(
    cloud,
    scalars=curve_points[:, 2],
    cmap="RdBu",
    point_size=point_size,
    render_points_as_spheres=True,
)
pl.enable_anti_aliasing("ssaa")
pl.camera_position = "xy"
pl.enable_parallel_projection()
pl.show()

In [5]:
curve_velocity = np.diff(np.append(curve_points, curve_points[:1], axis=0), axis=0)
if not closed_loop:
    curve_velocity[-1] = curve_velocity[0]
curve_tangent = curve_velocity / np.linalg.norm(curve_velocity, axis=1)[:, None]

curve_acceleration = np.diff(
    np.append(curve_tangent, curve_tangent[:1], axis=0), axis=0
)
if not closed_loop:
    curve_acceleration[-1] = curve_acceleration[0]
curve_curvature = np.linalg.norm(curve_acceleration, axis=1)
curve_normal = curve_acceleration / curve_curvature[:, None]

curve_binormal = np.cross(curve_tangent, curve_normal)
curve_binormal = curve_binormal / np.linalg.norm(curve_binormal, axis=1)[:, None]

v = np.linspace(0, 2 * np.pi, n_v, endpoint=not closed_loop)

tube_points = curve_points[:, None, :] + tube_radius * (
    curve_normal[:, None, :] * np.cos(v)[None, :, None]
    + curve_binormal[:, None, :] * np.sin(v)[None, :, None]
)
tube_points = tube_points.reshape(-1, 3)

In [ ]:
def torus_triangles(Nr, Nc):

    if closed_loop:
        out = np.empty((Nr, Nc, 2, 3), dtype=int)

        r = np.arange(Nr * Nc).reshape(Nr, Nc)
        r = np.concatenate((r, r[:, 0, None]), axis=1)
        r = np.concatenate((r, r[0, None, :]), axis=0)
    else:
        out = np.empty((Nr - 1, Nc - 1, 2, 3), dtype=int)
        r = np.arange(Nr * Nc).reshape(Nr, Nc)

    out[:, :, 0, 0] = r[:-1, :-1]
    out[:, :, 1, 0] = r[:-1, 1:]
    out[:, :, 0, 1] = r[:-1, 1:]

    out[:, :, 1, 1] = r[1:, 1:]
    out[:, :, :, 2] = r[1:, :-1, None]

    out.shape = (-1, 3)

    # Reshape the result as a list of faces
    out = np.concatenate((3 * np.ones((out.shape[0], 1), dtype=int), out), axis=1)
    return out.reshape(-1)


tube = pv.PolyData(tube_points, faces=torus_triangles(n_u, n_v))

pl = pv.Plotter(window_size=[400, 400])
pl.add_mesh(tube)
pl.camera_position = "xy"
pl.show()

U, V = np.meshgrid(u / (2 * np.pi), v / (2 * np.pi), indexing="ij")
tube.point_data["u"] = U.reshape(-1)
tube.point_data["v"] = V.reshape(-1)
tube.active_texture_coordinates = np.stack((U.reshape(-1), V.reshape(-1)), axis=1)

In [ ]:
S = pv.PolyData(tube_points, faces=torus_triangles(n_u, n_v))

pl = pv.Plotter(window_size=[200, 200])
pl.add_mesh(S, show_edges=False)
pl.camera_position = "xy"
pl.camera.zoom(1.4)
pl.enable_parallel_projection()
if False:
    pl.enable_anti_aliasing()
else:
    pl.disable_anti_aliasing()
pl.set_background("#FAFAFA")
pl.show()
pl.screenshot("images/pyvista_window.jpg");

In [ ]:
for anti_aliasing in [True, False]:

    pl = pv.Plotter(window_size=[200, 200])
    pl.add_mesh(S, show_edges=False)
    pl.camera_position = "xy"
    pl.camera.zoom(1.4)
    pl.enable_parallel_projection()
    if anti_aliasing:
        pl.enable_anti_aliasing()
    else:
        pl.disable_anti_aliasing()
    pl.set_background("#FAFAFA")
    pl.show()
    pl.screenshot(f"images/surface/0_antialiasing_{anti_aliasing}.png");

In [ ]:
for parallel_projection in [True, False]:

    pl = pv.Plotter(window_size=[200, 200])
    pl.add_mesh(S, show_edges=False)
    pl.camera_position = "xy"
    pl.camera.zoom(1.4)
    if parallel_projection:
        pl.enable_parallel_projection()
    else:
        pl.camera.view_angle = 30
    pl.set_background("#FAFAFA")
    pl.show()
    pl.screenshot(f"images/surface/0_parallel_{parallel_projection}.png");

In [ ]:
import os
print(os.getcwd())

In [12]:
tube.save("trefoil_lowres.stl")
tube.subdivide(4, subfilter="loop").save("trefoil_highres.stl")

In [ ]:
import matplotlib.pyplot as plt
import numpy as np

from matplotlib import cm
from matplotlib.ticker import LinearLocator

fig, ax = plt.subplots(subplot_kw={"projection": "3d"})

XYZ = tube.points

# Plot the surface.
surf = ax.plot_trisurf(XYZ[:, 0], XYZ[:, 1], XYZ[:, 2], triangles=tube.faces.reshape(-1, 4)[:, 1:])

# Customize the z axis.
#ax.set_zlim(-1.01, 1.01)
#ax.zaxis.set_major_locator(LinearLocator(10))
# A StrMethodFormatter is used automatically
#ax.zaxis.set_major_formatter('{x:.02f}')

# Add a color bar which maps values to colors.
#fig.colorbar(surf, shrink=0.5, aspect=5)

plt.show()

In [7]:
IMG_ID = 1

def display_surface(
    surface,
    style="surface",
    show_edges=False,
    line_width=2,
    lighting="light kit",
    subfilter="loop",
    nsub=None,
    smooth_shading=True,
    pbr=False,
    ambient=None,
    diffuse=None,
    metallic=None,
    roughness=None,
    cubemap=False,
    silhouette_width=None,
    scalars=None,
    cmap="RdBu_r",
    clim=None,
    rgb=False,
    texture=None,
    light_intensity=3.0,
    light_elev=40,
    light_azim=90,
    headlight_intensity=2.0,
    opacity=1.0,
    silhouette=None,
    shadows=None,
    parallel_projection=True,
    anti_aliasing=True,
    culling=None,
    filename=None,
):
    global IMG_ID
    if nsub is not None:
        surface = surface.subdivide(subfilter=subfilter, nsub=nsub)

    surface = surface.compute_normals()

    if pbr:
        lighting = "none"
    pl = pv.Plotter(window_size=[800, 800], lighting=lighting)

    if scalars == "z":
        scalars = surface.points[:, 2]
    elif scalars == "mean curvature":
        scalars = surface.curvature("mean")
    elif scalars == "gauss curvature":
        scalars = surface.curvature("gaussian")
    elif scalars == "xyz":
        scalars = surface.points
        rgb=True
    elif scalars == "normals":
        scalars = (surface.point_normals + 1) / 2
        rgb=True

    pl.add_mesh(
        surface,
        style=style,
        show_edges=show_edges,
        line_width=line_width,
        render_lines_as_tubes=False,
        color="lightblue" if (scalars is None and texture is None) else None,
        scalars=scalars,
        cmap=cmap,
        clim=clim,
        rgb=rgb,
        smooth_shading=smooth_shading,
        pbr=pbr,
        ambient=ambient,
        diffuse=diffuse,
        metallic=metallic,
        roughness=roughness,
        texture=pv.read_texture(texture) if texture is not None else None,
        culling=culling,
        opacity=opacity,
        silhouette=silhouette,
    )

    if silhouette_width is not None:
        surface["silhouette_width"] = silhouette_width * np.ones(surface.n_points)
        # Now use those normals to warp the surface
        silhouette = surface.warp_by_scalar(scalars="silhouette_width")

        pl.add_mesh(
            silhouette,
            color="black",
            culling="front",
            interpolation="pbr",
            roughness=1,
        )

    # elev = 0, azim = 0 is the +x direction
    # elev = 0, azim = 90 is the +y direction
    # elev = 90, azim = 0 is the +z direction
    if lighting == "none":
        n_lights = np.ceil(light_intensity).astype(int)

        light = pv.Light(intensity=light_intensity / n_lights)
        light.set_direction_angle(light_elev, light_azim)
        for _ in range(n_lights):
            pl.add_light(light)

        n_headlights = np.ceil(headlight_intensity).astype(int)
        light = pv.Light(
            light_type="headlight", intensity=headlight_intensity / n_headlights
        )
        for _ in range(n_headlights):
            pl.add_light(light)

    if cubemap:
        cubemap = pv.examples.download_sky_box_cube_map()
        #pl.add_actor(cubemap.to_skybox())
        pl.set_environment_texture(cubemap)

    if shadows == True:
        pl.enable_shadows()
    elif shadows == "ssao":
        pl.enable_ssao(radius=1)
    elif shadows == "edl":
        pl.enable_eye_dome_lighting()

    if anti_aliasing:
        pl.enable_anti_aliasing("ssaa", multi_samples=32)
    pl.camera_position = "xy"
    if parallel_projection:
        pl.enable_parallel_projection()
    if scalars is not None and not rgb:
        pl.remove_scalar_bar()
    pl.camera.zoom(1.4)
    pl.set_background("#FAFAFA")
    pl.show()
    if filename is not None:
        pl.screenshot(f"images/surface/{IMG_ID}_{filename}.jpg")
        IMG_ID += 1

In [ ]:
if False:
    display_surface(
        tube,
        nsub=0,
        smooth_shading=False,
        parallel_projection=False,
        light_intensity=.6,
        headlight_intensity=.6,
        filename=f"data_noparallel",
    )

display_surface(
    tube,
    nsub=0,
    smooth_shading=False,
    light_intensity=.6,
    headlight_intensity=.6,
    filename=f"data_raw",
)

display_surface(
    tube,
    nsub=0,
    smooth_shading=True,
    filename=f"data_smooth",
)

In [ ]:
for subfilter in ["linear", "loop"]:
    for nsub in range(0, 5):
        for style in ["raw", "smooth"]:
            display_surface(
                tube,
                nsub=nsub,
                subfilter=subfilter,
                show_edges=(style == "raw"),
                line_width=4 if nsub < 2 else 2,
                smooth_shading=(style == "smooth"),
                filename=f"subdivision_{subfilter}_{style}_{nsub}",
            )

In [ ]:
for cmap in ["viridis", "plasma", "coolwarm", "bwr", "RdBu", "RdBu_r"]:
    display_surface(
        tube,
        nsub=4,
        scalars="gauss curvature",
        cmap=cmap,
        clim=(-1, 1),
        ambient=0,
        diffuse=1,
        #shadows="ssao",
        filename=f"signal_{cmap}",
    )

In [ ]:
for ambient in [0, 0.1, 0.2]:
    for diffuse in [1]:
        display_surface(
                tube,
                nsub=4,
                scalars="gauss curvature",
                clim=(-1, 1),
                ambient=ambient,
                diffuse=diffuse,
                #shadows="ssao",
                filename=f"ambient_{ambient}",
            )

In [ ]:
for light_ratio in [-0.5, 0, 0.5]:
    display_surface(
        tube,
        nsub=4,
        scalars="gauss curvature",
        clim=(-1, 1),
        light_elev=40,
        light_azim=90,
        lighting="none",
        light_intensity=0.7 - light_ratio,
        headlight_intensity=0.7 + light_ratio,
        #shadows="ssao",
        filename=f"light_ratio_{light_ratio}",
        )

In [ ]:
for shadows in [False, True, "ssao", "edl"]:
    display_surface(
        tube,
        nsub=4,
        scalars="gauss curvature",
        clim=(-1, 1),
        lighting="none",
        light_intensity=0.7,
        headlight_intensity=0.7,
        #pbr=True,
        #metallic=0.,
        #roughness=0.7,
        shadows=shadows,
        filename=f"shadows_{shadows}",
        )

In [ ]:
for cubemap in [False, True]:
    for metallic in [0., 0.5, 1.]:
        for roughness in [0.2, 0.4, 0.8]:
            display_surface(
                tube,
                nsub=4,
                scalars="gauss curvature",
                clim=(-1, 1),
                pbr=True,
                ambient=0.2,
                metallic=metallic,
                roughness=roughness,
                light_intensity=3 + 2 * metallic,
                headlight_intensity=2 + 2 * metallic,
                cubemap=cubemap,
                shadows="ssao",
                filename=f"pbr_metallic_{metallic}_roughness_{roughness}_cubemap_{cubemap}",
                )

In [ ]:
display_surface(
    tube,
    nsub=4,
    scalars="gauss curvature",
    cmap="RdBu_r",
    clim=(-1, 1),
    silhouette=dict(
        color='black',
        line_width=10.0,
    ),
    ambient=0.,
    diffuse=1,
    pbr=True,
    metallic=0.,
    roughness=0.7,
    shadows="ssao",
    filename="silhouette_filter",
)

In [ ]:
for silhouette_width in [0., 0.01, 0.02, 0.05]:
    display_surface(
        tube,
        nsub=4,
        scalars="gauss curvature",
        cmap="RdBu_r",
        clim=(-1, 1),
        silhouette_width=silhouette_width,
        ambient=0.,
        diffuse=1,
        pbr=True,
        metallic=0.,
        roughness=0.7,
        shadows="ssao",
        filename=f"silhouette_{silhouette_width}",
    )

In [ ]:
display_surface(
    tube,
    nsub=4,
    scalars="xyz",
    clim=(-1, 1),
    silhouette_width=0.02,
    ambient=0.,
    diffuse=1,
    pbr=True,
    metallic=0.,
    roughness=0.7,
    shadows=True,
    filename="xyz",
)


display_surface(
    tube,
    nsub=4,
    scalars="normals",
    clim=(-1, 1),
    silhouette_width=0.02,
    ambient=0.,
    diffuse=1,
    pbr=True,
    metallic=0.,
    roughness=0.7,
    shadows=True,
    filename="normals",
)

In [ ]:
tube.active_texture_coordinates = np.stack((U.reshape(-1), .125 * V.reshape(-1)), axis=1)

display_surface(
    tube,
    nsub=4,
    scalars="u",
    cmap="RdBu_r",
    clim=(0, 1),
    silhouette_width=0.02,
    ambient=0.,
    diffuse=1,
    pbr=True,
    metallic=0.,
    roughness=0.7,
    shadows="ssao",
    filename="texture_U",
)


display_surface(
    tube,
    nsub=4,
    scalars="v",
    cmap="RdBu_r",
    clim=(0, 1),
    silhouette_width=0.02,
    ambient=0.,
    diffuse=1,
    pbr=True,
    metallic=0.,
    roughness=0.7,
    shadows="ssao",
    filename="texture_V",
)



display_surface(
    tube,
    nsub=4,
    scalars=None,
    silhouette_width=0.02,
    ambient=0.1,
    diffuse=1,
    lighting="none",
    light_intensity=1.0,
    headlight_intensity=1.0,
    shadows=True,
    texture="bricks.jpg",
    filename="bricks"
)

In [ ]:
pl = pv.Plotter(window_size=[800, 800], lighting="none")
pl.import_gltf("stone_tiles_02_1k/stone_tiles_02_1k.gltf")


light_intensity = 4.5
headlight_intensity = 1.5

n_lights = np.ceil(light_intensity).astype(int)

light = pv.Light(intensity=light_intensity / n_lights)
light.set_direction_angle(40, 90)
for _ in range(n_lights):
    pl.add_light(light)

n_headlights = np.ceil(headlight_intensity).astype(int)
light = pv.Light(
    light_type="headlight", intensity=headlight_intensity / n_headlights
)
for _ in range(n_headlights):
    pl.add_light(light)


pl.enable_anti_aliasing("ssaa", multi_samples=32)
pl.set_background("#FAFAFA")
pl.camera.zoom(1.5)
pl.show()
pl.screenshot(f"images/surface/{IMG_ID}_gltf.jpg")
IMG_ID += 1

In [20]:
if False:
    smooth_tube = tube.subdivide(subfilter="loop", nsub=3)

    smooth_tube.faces.reshape(-1, 4)[:, 1:]

    # Create adjacency matrix
    n_points = smooth_tube.n_points
    n_faces = smooth_tube.n_cells

    # adjacency is a sparse matrix
    import scipy.sparse as sp
    adjacency = sp.lil_array((n_points, n_points), dtype=np.float64)

    for face in smooth_tube.faces.reshape(-1, 4)[:, 1:]:
        for i in range(3):
            adjacency[face[i], face[(i + 1) % 3]] += 1
            adjacency[face[(i + 1) % 3], face[i]] += 1

    adjacency = adjacency.tocsr()
    adjacency = adjacency / adjacency.sum(axis=1)[:, None]

    smooth_tube = smooth_tube.compute_normals()
    smooth_tube = smooth_tube.compute_normals()
    mean_curv = smooth_tube.curvature("mean")
    n = smooth_tube.point_normals

    #smooth_tube["vectors"] = .1 * mean_curv[:, None] * smooth_tube.point_normals
    #smooth_tube.set_active_vectors("vectors")

    smooth_tube["mean curvature"] = smooth_tube.curvature("mean")

    max_curve = np.max(np.abs(mean_curv))
    smooth_tube["scale"] = - .1 * mean_curv / max_curve
    smooth_tube["normals"] = smooth_tube.point_normals
    arrows = smooth_tube.glyph(scale="scale", orient="normals", tolerance=0.01)

    pl = pv.Plotter(window_size=[800, 800], lighting="none")

    #pl.add_mesh(arrows, lighting=False, cmap="RdBu_r", clim=[-1, 1])
    #pl.add_mesh(arrows, lighting=False, cmap="RdBu_r", clim=[-1, 1])

    pl.add_mesh(smooth_tube,
                scalars="mean curvature",
                #opacity=0.5,
                pbr=True,
                metallic=0.0,
                roughness=0.4,
                cmap="RdBu_r",
                clim=(-2, 2),
                )



    # elev = 0, azim = 0 is the +x direction
    # elev = 0, azim = 90 is the +y direction
    # elev = 90, azim = 0 is the +z direction
    light_intensity = 3.0
    headlight_intensity = 2.0
    n_lights = np.ceil(light_intensity).astype(int)

    light = pv.Light(intensity=light_intensity / n_lights)
    light.set_direction_angle(40, 90)
    for _ in range(n_lights):
        pl.add_light(light)

    n_headlights = np.ceil(headlight_intensity).astype(int)
    light = pv.Light(
        light_type="headlight", intensity=headlight_intensity / n_headlights
    )
    for _ in range(n_headlights):
        pl.add_light(light)


    silhouette_width = .01
    if silhouette_width is not None:
        smooth_tube["silhouette_width"] = silhouette_width * np.ones(smooth_tube.n_points)
        # Now use those normals to warp the surface
        silhouette = smooth_tube.warp_by_scalar(scalars="silhouette_width")

        pl.add_mesh(
            silhouette,
            color="black",
            culling="front",
            interpolation="pbr",
            roughness=1,
        )

    pl.enable_ssao(radius=1)
    pl.enable_anti_aliasing("ssaa", multi_samples=32)
    pl.camera_position = "xy"
    pl.enable_parallel_projection()
    pl.camera.zoom(1.4)
    pl.set_background("#FAFAFA")
    #pl.remove_scalar_bar("scale")
    pl.remove_scalar_bar("mean curvature")


    pl.open_movie("images/curvature_flow.mp4", quality=10)

    for it in range(1000):
        #smooth_tube.points = .5 * (smooth_tube.points + adjacency @ smooth_tube.points)
        smooth_tube.points += 1 * (adjacency @ smooth_tube.points - smooth_tube.points)
        #smooth_tube.smooth(inplace=True, relaxation_factor=.5, n_iter=10)
        smooth_tube["mean curvature"] = smooth_tube.curvature("gaussian")

        # smooth_tube["mean curvature"] = (adjacency @ smooth_tube["mean curvature"])

        max_curve = np.max(np.abs(mean_curv))
        smooth_tube["scale"] = - .01 * mean_curv / max_curve
        smooth_tube["normals"] = smooth_tube.point_normals
        smooth_tube["vectors"] = smooth_tube["scale"][:, None] * smooth_tube.point_normals

        #arrows.points = smooth_tube.glyph(scale="scale", orient="normals", tolerance=0.01)

        if silhouette_width is not None:
            silhouette_width = .01 * smooth_tube.points.std()
            smooth_tube["silhouette_width"] = silhouette_width * np.ones(smooth_tube.n_points)
            silhouette.points = smooth_tube.warp_by_scalar(scalars="silhouette_width").points

        #pl.add_text(f"iteration {it}", name='time-label')
        pl.write_frame()

    pl.close()